In [1]:
import os
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow import keras
from collections import deque
import matplotlib.pyplot as plt


from tensorflow import keras
from tensorflow.keras import layers

from tensorflow.keras.layers import *
from tensorflow.keras.models import Sequential
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint
from tensorflow.keras.utils import plot_model
from sklearn.preprocessing import LabelEncoder

from keras.models import Model


import cv2
import mediapipe as mp

os.environ['KMP_DUPLICATE_LIB_OK']='True'



2025-05-21 12:38:13.497501: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1747831093.519003 2165380 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1747831093.525949 2165380 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-05-21 12:38:13.548991: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
import tensorflow as tf

# TensorFlow version
tf_version = tf.__version__

# CUDA and cuDNN versions
cuda_version = tf.sysconfig.get_build_info().get("cuda_version", "Not found")
cudnn_version = tf.sysconfig.get_build_info().get("cudnn_version", "Not found")

print(f"TensorFlow version: {tf_version}")
print(f"CUDA version: {cuda_version}")
print(f"cuDNN version: {cudnn_version}")


TensorFlow version: 2.18.0
CUDA version: 12.5.1
cuDNN version: 9


In [3]:
dataset_dir = "../../../UCF50"

training_ratio = 0.6
validation_ratio = 0.25
test_ratio = 0.15
# classes =['PullUps','Punch','PushUps','HighJump','JavelinThrow']
# num_classes = len(classes)

number_of_frames=15

In [4]:
def extract_ucf50_classes(dataset_dir):
    classes = [folder for folder in os.listdir(dataset_dir) if os.path.isdir(os.path.join(dataset_dir, folder))]
    return classes

classes = extract_ucf50_classes(dataset_dir)
num_classes = len(classes)

label_encoder=LabelEncoder()
label_encoder.fit(classes)


# classes = classes[:3]
# num_classes = len(classes)

LabelEncoder()

In [5]:

def get_video_paths_and_categories(root_dir):
    training_video_paths = []
    training_targets = []
    validation_video_paths = []
    validation_targets = []
    test_video_paths = []
    test_targets = []
    

    for category in classes:
        category_path = os.path.join(root_dir, category)
        
        if os.path.isdir(category_path):
            nvideos = len(os.listdir(category_path))
            if nvideos == 0:
                print(f"No videos found for category: {category}")
                continue

            
            training_count = int(nvideos * training_ratio)
            validation_count = int(nvideos * validation_ratio)
            test_count = nvideos - (training_count + validation_count) 
            
            label = label_encoder.transform([category])[0]
            
            video_files = os.listdir(category_path)
            
            
            for i in range(training_count):
                video_file = video_files[i]
                video_path = os.path.join(category_path, video_file)
                training_video_paths.append(video_path)
                training_targets.append(label)

            for i in range(training_count, training_count + validation_count):
                video_file = video_files[i]
                video_path = os.path.join(category_path, video_file)
                validation_video_paths.append(video_path)
                validation_targets.append(label)

            for i in range(training_count + validation_count, training_count + validation_count + test_count):
                video_file = video_files[i]
                video_path = os.path.join(category_path, video_file)
                test_video_paths.append(video_path)
                test_targets.append(label)

        else:
            print(f"No class found for {category}")

    return (training_video_paths, training_targets, 
            validation_video_paths, validation_targets, 
            test_video_paths, test_targets)



In [ ]:

# mp_pose = mp.solutions.pose
# def apply_mediapipe_pose(video_path,number_of_frames=10):
 
#     cap = cv2.VideoCapture(video_path)
    
#     if not cap.isOpened():
#         print("Error: Could not open video.")
#         return []

#     total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
#     step=total_frames//number_of_frames
    
#     pose_landmarks_list = []
    
#     index=-1
#     frames_count=0
#     with mp_pose.Pose(static_image_mode=False, min_detection_confidence=0.5, min_tracking_confidence=0.5) as pose:
#         while True:
#             ret, frame = cap.read()
#             if not ret:
#                 break

#             index+=1
            
#             if index % step == 0 and frames_count<number_of_frames:
#                 frames_count+=1

#                 rgb_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
#                 rgb_frame.flags.writeable = False

#                 results = pose.process(rgb_frame)

#                 rgb_frame.flags.writeable = True
#                 if results.pose_landmarks:
#                     mp.solutions.drawing_utils.draw_landmarks(
#                         frame, results.pose_landmarks, mp_pose.POSE_CONNECTIONS)

#                     landmarks = results.pose_landmarks.landmark
#                     pose_landmarks_list.append([(lm.x, lm.y, lm.z,lm.visibility) for lm in landmarks])


#                 #gray_frame = cv2.cvtColor(frame, cv2.COLOR_RGB2GRAY)
#                 # cv2.imshow('MediaPipe Pose', gray_frame)
#                 # cv2.imshow('MediaPipe Pose', frame)
#                 # if cv2.waitKey(10) & 0xFF == ord('q'):
#                 #     break
           
    
#     #padding
            
#     if len(pose_landmarks_list) < number_of_frames and len(pose_landmarks_list) > 0:
#         x=-1
#         while len(pose_landmarks_list) < number_of_frames:
#             pose_landmarks_list.append(pose_landmarks_list[x])
#             x-=1

#     cap.release()
#     cv2.destroyAllWindows()

#     # return pose_landmarks_list
#     return np.array(pose_landmarks_list)



In [ ]:
def apply_mediapipe_pose_v2(video_path, number_of_frames=15):
    mp_pose = mp.solutions.pose
    cap = cv2.VideoCapture(video_path)
    
    if not cap.isOpened():
        print("Error: Could not open video.")
        return []

    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    step = total_frames // number_of_frames
    
    pose_landmarks_list = []
    selected_frame_indices=[]
    
    
    with mp_pose.Pose(static_image_mode=False, min_detection_confidence=0.5, min_tracking_confidence=0.5) as pose:
        # Calculate the frame range for each area and choose the first frame that has pose landmarks
        for i in range(number_of_frames):
            start_frame = i * step
            end_frame = (i + 1) * step if (i + 1) < number_of_frames else total_frames
            
            # Try to find a frame with pose landmarks within the area
            frame_with_landmarks = False
            
            for frame_index in range(start_frame, end_frame):
                cap.set(cv2.CAP_PROP_POS_FRAMES, frame_index)
                ret, frame = cap.read()
                if not ret:
                    break

                # frame =cv2.resize(frame,image_shape)

                rgb_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
                rgb_frame.flags.writeable = False
                results = pose.process(rgb_frame)

                rgb_frame.flags.writeable = True
                if results.pose_landmarks:
                    # Pose landmarks found, add the frame's landmarks to the list
                    landmarks = results.pose_landmarks.landmark
                    pose_landmarks_list.append([(lm.x, lm.y, lm.z, lm.visibility,lm.presence) for lm in landmarks])
                    selected_frame_indices.append(frame_index)
                    frame_with_landmarks = True
                    break  # Once we find the first frame with landmarks, break the loop for this area

            # If no frame with landmarks was found, we add None or some default padding (optional)
            # if not frame_with_landmarks:
            #     # 
            #     pose_landmarks_list.append(pose_landmarks_list[-1])
            #     selected_frame_indices.append(selected_frame_indices[-1])

    cap.release()
    cv2.destroyAllWindows()

    # Padding if the number of frames is less than required
    if len(pose_landmarks_list) < number_of_frames and len(pose_landmarks_list) > 0:
        x = -1
        while len(pose_landmarks_list) < number_of_frames:
            
            if pose_landmarks_list[x] == pose_landmarks_list[-1]:
                x=x-1
            
            pose_landmarks_list.append(pose_landmarks_list[x])
            selected_frame_indices.append(selected_frame_indices[x])
            x -= 1

    return np.array(pose_landmarks_list),np.array(selected_frame_indices)

In [7]:


x_train, y_train, x_val, y_val, x_test, y_test = get_video_paths_and_categories(dataset_dir)
# video_paths, targets = get_video_paths_and_categories(dataset_dir)

In [10]:
len(x_train)

3992

In [11]:

import concurrent.futures

# Initialize start indices and number of items per worker
train_size = len(x_train)
val_size = len(x_val)
test_size = len(x_test)

P = 48
train_startof=[None]*P
val_startof=[None]*P
test_startof=[None]*P

train_nof=[train_size // P] * P
val_nof=[val_size // P] * P
test_nof=[test_size // P] * P

train_startof[0]=0
val_startof[0]=0
test_startof[0]=0



for i in range(P):
    if i < train_size % P:
        train_nof[i] += 1
    if i < val_size % P:
        val_nof[i] += 1
    if i < test_size % P:
        test_nof[i] += 1
    
    if i > 0:
        train_startof[i] = train_startof[i - 1] + train_nof[i - 1]
        val_startof[i] = val_startof[i - 1] + val_nof[i - 1]
        test_startof[i] = test_startof[i - 1] + test_nof[i - 1]


# Worker function to process a chunk of the data
def worker(tid):
    
    # print(f"Worker {tid} started")
    
    train_start=train_startof[tid]
    train_n=train_nof[tid]
    val_start=val_startof[tid]
    val_n=val_nof[tid]
    test_start=test_startof[tid]
    test_n=test_nof[tid]
    
    train_end=train_start+train_n
    val_end=val_start+val_n
    test_end=test_start+test_n
    
    train_x=[]
    train_y=[]
    val_x=[]
    val_y=[]
    test_x=[]
    test_y=[]
    
    for i in range(train_start, train_end):
        video_path = x_train[i]
        target = y_train[i]
        pose_landmarks,i = apply_mediapipe_pose_v2(video_path,number_of_frames)
        if len(pose_landmarks) == number_of_frames:
            train_x.append(pose_landmarks)
            train_y.append(target)
            
    for i in range(val_start, val_end):
        video_path = x_val[i]
        target = y_val[i]
        pose_landmarks,i = apply_mediapipe_pose_v2(video_path,number_of_frames)
        if len(pose_landmarks) == number_of_frames:
            val_x.append(pose_landmarks)
            val_y.append(target)
            
    for i in range(test_start, test_end):
        video_path = x_test[i]
        target = y_test[i]
        pose_landmarks,i = apply_mediapipe_pose_v2(video_path,number_of_frames)
        if len(pose_landmarks) == number_of_frames:
            test_x.append(pose_landmarks)
            test_y.append(target)
            
    return tid, train_x, train_y, val_x, val_y, test_x, test_y
            
    
 
    # for idx in range(startof[i], startof[i] + nof[i]):
    #     video_path = video_paths[idx]
    #     target = targets[idx]
    #     pose_landmarks = apply_mediapipe_pose(video_path,number_of_frames)
    #     if len(pose_landmarks) == P:
    #         local_x.append(pose_landmarks)
    #         local_y.append(target)
    # return i, local_x, local_y

with concurrent.futures.ThreadPoolExecutor(max_workers=P) as executor:
    results = list(executor.map(worker, range(P)))



I0000 00:00:1747833234.832157 2600136 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1747833234.908493 2600316 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 535.230.02), renderer: NVIDIA A40/PCIe/SSE2
I0000 00:00:1747833234.931680 2600120 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1747833234.988740 2600430 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 535.230.02), renderer: NVIDIA A40/PCIe/SSE2
I0000 00:00:1747833234.989890 2600118 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
W0000 00:00:1747833235.022427 2600277 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1747833235.040813 2600335 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
I0000 00:00:1747833235.051297 2

In [12]:
sorted_results = sorted(results, key=lambda x: x[0])

def get_shape(lst):
    if isinstance(lst, list):
        return [len(lst)] + get_shape(lst[0]) if lst else []
    return []

x_train_data = []
y_train_data = []
x_val_data = []
y_val_data = []
x_test_data = []
y_test_data = []

for result in sorted_results:
    i, worker_train_x, worker_train_y, worker_val_x, worker_val_y, worker_test_x, worker_test_y = result
    # Fill the respective ranges in the corresponding arrays
    x_train_data[train_startof[i]:train_startof[i] + train_nof[i]] = worker_train_x
    y_train_data[train_startof[i]:train_startof[i] + train_nof[i]] = worker_train_y
    x_val_data[val_startof[i]:val_startof[i] + val_nof[i]] = worker_val_x
    y_val_data[val_startof[i]:val_startof[i] + val_nof[i]] = worker_val_y
    x_test_data[test_startof[i]:test_startof[i] + test_nof[i]] = worker_test_x
    y_test_data[test_startof[i]:test_startof[i] + test_nof[i]] = worker_test_y

In [13]:

x_train_data = np.array(x_train_data)
y_train_data = np.array(y_train_data)
x_val_data = np.array(x_val_data)
y_val_data = np.array(y_val_data)
x_test_data = np.array(x_test_data)
y_test_data = np.array(y_test_data)

In [14]:
x_test_data.shape

(949, 15, 33, 5)

In [15]:
#save data


np.save('../x_train_data.npy', x_train_data)
np.save('../y_train_data.npy', y_train_data)
np.save('../x_val_data.npy', x_val_data)
np.save('../y_val_data.npy', y_val_data)
np.save('../x_test_data.npy', x_test_data)
np.save('../y_test_data.npy', y_test_data)

In [23]:
#load data


x_train_data = np.load('../x_train_data.npy', allow_pickle=True)
y_train_data = np.load('../y_train_data.npy', allow_pickle=True)
x_val_data = np.load('../x_val_data.npy', allow_pickle=True)
y_val_data = np.load('../y_val_data.npy', allow_pickle=True)
x_test_data = np.load('../x_test_data.npy', allow_pickle=True)
y_test_data = np.load('../y_test_data.npy', allow_pickle=True)

pose_landmarks_channels = x_train_data.shape[3]
pose_landmarks_channels

5

In [16]:
def hip_center_and_normalize(pl):
   
    data=pl.copy()
    coordinates = data[:, :, :, :3]  
    visibility = data[:, :, :, 3:4]  
    presence = data[:, :, :, 4:5]  

    
    left_hip = coordinates[:, :, 23, :] 
    right_hip = coordinates[:, :, 24, :] 
    hip_center = (left_hip + right_hip) / 2 
    # hip_center_z=hip_center[:,:,2]

    # batch , n_frames, n_landmarks, 5

    centered_coords = coordinates.copy()
    

    hip_center = hip_center[:, :, None, :]
    centered_coords -= hip_center

    
    x_values = centered_coords[:, :, :, 0]  
    y_values = centered_coords[:, :, :, 1]  
    z_values = centered_coords[:, :, :, 2]  
    
    x_min=np.min(x_values,keepdims=True,axis=2)
    x_max=np.max(x_values,keepdims=True,axis=2)
    x_size=np.abs(x_max-x_min)
    x_max_size=np.max(x_size,keepdims=True,axis=1)
    
    y_min=np.min(y_values,keepdims=True,axis=2)
    y_max=np.max(y_values,keepdims=True,axis=2)
    y_size=np.abs(y_max-y_min)
    y_max_size=np.max(y_size,keepdims=True,axis=1)
    
    z_min=np.min(z_values,keepdims=True,axis=2)
    z_max=np.max(z_values,keepdims=True,axis=2)
    z_size=np.abs(z_max-z_min)   
    z_max_size=np.max(z_size,keepdims=True,axis=1)


    epsilon = 1e-8
    
    x_values /= (x_max_size + epsilon)
    y_values /= (y_max_size + epsilon)
    z_values /= (z_max_size + epsilon)
    
    centered_coords[:, :, :, 0] = x_values
    centered_coords[:, :, :, 1] = y_values
    centered_coords[:, :, :, 2] = z_values
    
    processed_data = np.concatenate([centered_coords, visibility, presence], axis=3)

    return processed_data

In [17]:
x_train_data.shape, y_train_data.shape, x_val_data.shape, y_val_data.shape, x_test_data.shape, y_test_data.shape

((3716, 15, 33, 5),
 (3716,),
 (1534, 15, 33, 5),
 (1534,),
 (949, 15, 33, 5),
 (949,))

In [24]:
pose_landmarks_channels = x_train_data.shape[3]
x_train_data=hip_center_and_normalize(x_train_data)
x_val_data=hip_center_and_normalize(x_val_data)
x_test_data=hip_center_and_normalize(x_test_data)

In [10]:
x_train_data.shape, y_train_data.shape, x_val_data.shape, y_val_data.shape, x_test_data.shape, y_test_data.shape

((3716, 15, 33, 5),
 (3716,),
 (1534, 15, 33, 5),
 (1534,),
 (949, 15, 33, 5),
 (949,))

In [25]:
# reshape data
# x_train_reshaped = np.array(x_train).reshape(len(x_train), number_of_frames,33*3).astype('float32')
# x_val_reshaped = np.array(x_val).reshape(len(x_val), number_of_frames,33*3).astype('float32')
# x_test_reshaped = np.array(x_test).reshape(len(x_test), number_of_frames,33*3).astype('float32')

x_train_reshaped = x_train_data.reshape(x_train_data.shape[0], number_of_frames,33*pose_landmarks_channels).astype('float32')
x_val_reshaped = x_val_data.reshape(x_val_data.shape[0], number_of_frames,33*pose_landmarks_channels).astype('float32')
x_test_reshaped = x_test_data.reshape(x_test_data.shape[0], number_of_frames,33*pose_landmarks_channels).astype('float32')

In [15]:
x_test_data.shape

(531, 15, 33, 4)

In [26]:
x_train_reshaped.shape, x_val_reshaped.shape, x_test_reshaped.shape

((3716, 15, 165), (1534, 15, 165), (949, 15, 165))

In [ ]:
#BETS DON T TOUCH

import tensorflow as tf
from tensorflow.keras.layers import Input, Dense, LSTM, Dropout, MultiHeadAttention, LayerNormalization, Add, Bidirectional
from tensorflow.keras.models import Model

def make_transformer_scratch_classifier(input_shape):
    # input_layer = keras.layers.Input(input_shape)

    # conv1 = keras.layers.Conv1D(filters=256, kernel_size=3, padding="same")(input_layer)
    # conv1 = keras.layers.BatchNormalization()(conv1)
    # conv1 = keras.layers.ReLU()(conv1)

    # conv1 = keras.layers.Conv1D(filters=128, kernel_size=3, padding="same")(input_layer)
    # conv1 = keras.layers.BatchNormalization()(conv1)
    # conv1 = keras.layers.ReLU()(conv1)

    # conv1 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(input_layer)
    # conv1 = keras.layers.BatchNormalization()(conv1)
    # conv1 = keras.layers.ReLU()(conv1)

    # conv2 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(conv1)
    # conv2 = keras.layers.BatchNormalization()(conv2)
    # conv2 = keras.layers.ReLU()(conv2)

    # conv3 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(conv2)
    # conv3 = keras.layers.BatchNormalization()(conv3)
    # conv3 = keras.layers.ReLU()(conv3)
    
    input_layer = keras.layers.Input(input_shape)

    conv1 = keras.layers.Conv1D(filters=256, kernel_size=3, padding="same")(input_layer)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.ReLU()(conv1)

    conv2 = keras.layers.Conv1D(filters=128, kernel_size=3, padding="same")(conv1)
    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.ReLU()(conv2)

    conv3 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(conv2)
    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.ReLU()(conv3)

    conv4 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(conv3)
    conv4 = keras.layers.BatchNormalization()(conv4)
    conv4 = keras.layers.ReLU()(conv4)

    conv5 = keras.layers.Conv1D(filters=64, kernel_size=3, padding="same")(conv4)
    conv5 = keras.layers.BatchNormalization()(conv5)
    conv5 = keras.layers.ReLU()(conv5)

    gap = keras.layers.GlobalAveragePooling1D()(conv5)

    output_layer = keras.layers.Dense(num_classes, activation="softmax")(gap)

    return keras.models.Model(inputs=input_layer, outputs=output_layer)


In [27]:
input_shape = x_train_reshaped.shape[1:]
scratch_transformer_model = make_1dcnn_classifier(input_shape)


callbacks = [
    keras.callbacks.ModelCheckpoint(
        "1d_cnn_padded.keras", save_best_only=True, monitor="val_loss"
    ),
    keras.callbacks.ReduceLROnPlateau(
        monitor="val_loss", factor=0.5, patience=20, min_lr=0.0001
    ),
    keras.callbacks.EarlyStopping(monitor="val_loss", patience=50, verbose=1),
]
scratch_transformer_model.compile(
    optimizer="adam",
    loss="sparse_categorical_crossentropy",
    metrics=["accuracy"],
)

W0000 00:00:1747837476.443256 2165380 gpu_device.cc:2344] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


In [28]:
scratch_transformer_model.fit(
    x_train_reshaped,
    y_train_data,
    validation_data=(x_val_reshaped, y_val_data),
    epochs=500,
    batch_size=32,
    callbacks=callbacks,
    verbose=1,
)

Epoch 1/500
117/117 ━━━━━━━━━━━━━━━━━━━━ 5s 19ms/step - accuracy: 0.1226 - loss: 3.6059 - val_accuracy: 0.1643 - val_loss: 3.3814 - learning_rate: 0.0010
Epoch 2/500
117/117 ━━━━━━━━━━━━━━━━━━━━ 2s 16ms/step - accuracy: 0.2853 - loss: 2.8484 - val_accuracy: 0.2008 - val_loss: 3.1379 - learning_rate: 0.0010
Epoch 3/500
117/117 ━━━━━━━━━━━━━━━━━━━━ 2s 16ms/step - accuracy: 0.3387 - loss: 2.5549 - val_accuracy: 0.2373 - val_loss: 2.8588 - learning_rate: 0.0010
Epoch 4/500
117/117 ━━━━━━━━━━━━━━━━━━━━ 2s 15ms/step - accuracy: 0.3926 - loss: 2.2844 - val_accuracy: 0.2412 - val_loss: 3.0058 - learning_rate: 0.0010
Epoch 5/500
117/117 ━━━━━━━━━━━━━━━━━━━━ 2s 15ms/step - accuracy: 0.4427 - loss: 2.1190 - val_accuracy: 0.2653 - val_loss: 2.8740 - learning_rate: 0.0010
Epoch 6/500
117/117 ━━━━━━━━━━━━━━━━━━━━ 2s 15ms/step - accuracy: 0.4661 - loss: 1.9884 - val_accuracy: 0.2490 - val_loss: 2.9408 - learning_rate: 0.0010
Epoch 7/500
117/117 ━━━━━━━━━━━━━━━━━━━━ 2s 16ms/step - accuracy: 0.4992 - l

In [29]:

test_loss, test_accuracy = scratch_transformer_model.evaluate(x_test_reshaped, y_test_data, verbose=1)
print(f"Test Loss: {test_loss:.4f}")
print(f"Test Accuracy: {test_accuracy:.4f}")

30/30 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.5077 - loss: 2.9436
Test Loss: 2.5887
Test Accuracy: 0.5659


In [16]:


test_loss, test_accuracy = scratch_transformer_model.evaluate(x_test_reshaped, y_test_data, verbose=1)
print(f"Test Loss: {test_loss:.4f}")
print(f"Test Accuracy: {test_accuracy:.4f}")

 1/30 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step - accuracy: 0.3438 - loss: 3.9629

30/30 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - accuracy: 0.5196 - loss: 2.8775
Test Loss: 2.4902
Test Accuracy: 0.5774
